![Callysto.ca Banner](https://github.com/callysto/curriculum-notebooks/blob/master/callysto-notebook-banner-top.jpg?raw=true)

<a href="https://hub.callysto.ca/jupyter/hub/user-redirect/git-pull?repo=https%3A%2F%2Fgithub.com%2Fcallysto%2Fcurriculum-notebooks&branch=master&subPath=SocialStudies/GeographyAmericanRevolution/geographic-progression-american-revolution.ipynb&depth=1" target="_parent"><img src="https://raw.githubusercontent.com/callysto/curriculum-notebooks/master/open-in-callysto-button.svg?sanitize=true" width="123" height="24" alt="Open in Callysto"/></a>

# Geographic Progression of The American Revolution


The American Revolution (1775-83) is also known as the American Revolutionary War and the U.S. War of Independence. 

On July 4, 1776, America's Thirteen Colonies declared that they were no longer part of Britain. The British disagreed. A war between Britain and the Thirteen Colonies began as a result of this disagreement. This war was known as the American Revolution or the War of Independence. (From "Our Land and People", Patricia Shields-Ramsay, Douglas Ramsay)


> ![map of colonies](images/13_colonies.jpg)
>
> The location of the original thirteen English Colonies on the east coast of what is now known as the United States of America. 

In order to understand the origins and progression of the American Revolutionary War, we will look at the locations of various battles during each stage of the war. From this data, we can begin to understand where the battles were taking place, where they moved to, and try and understand the events surrounding them. To begin, we first need to download [an open data set from Wikipedia](https://en.wikipedia.org/wiki/List_of_American_Revolutionary_War_battles) that contains the locations and other information about the battles.

Select the code cell below, then click the `▶Run` button in the toolbar to download and display the data.

In [1]:
url = 'https://en.wikipedia.org/wiki/List_of_American_Revolutionary_War_battles'
import pandas as pd
revolution_data = pd.read_html(url)[17] # get the 18th table from the page
revolution_data

Battle                            Date  \
0                         Powder Alarm*               September 1, 1774   
1    Storming of Fort William and Mary*               December 14, 1774   
2      Battles of Lexington and Concord                  April 19, 1775   
3                       Siege of Boston  April 19, 1775 –March 17, 1776   
4                   Gunpowder Incident*                  April 20, 1775   
..                                  ...                             ...   
253            Action of 2 January 1783                 January 2, 1783   
254           Action of 22 January 1783                January 22, 1783   
255          Action of 15 February 1783               February 15, 1783   
256          Action of 17 February 1783                17 February 1783   
257            Recapture of the Bahamas                14–18 April 1783   

      Colony/State                                            Outcome  
0    Massachusetts          British soldiers remove military supplies  
1    New Hampshire  Patriots seize powder and shot after brief ski...  
2    Massachusetts  Patriot victory: British forces raiding Concor...  
3    Massachusetts  Patriot victory: British eventually evacuate B...  
4         Virginia  Virginia governor Lord Dunmore removes powder ...  
..             ...                                                ...  
253     Hispaniola                                       Inconclusive  
254       Virginia                                    British victory  
255     Guadeloupe                                    British victory  
256           Cuba                                    British victory  
257        Bahamas                                    British victory  

[258 rows x 4 columns]

From the table above we see that there is a lot of information to digest. There are 253 rows and four columns. The columns are the name of the battle, the date of the battle, where it took place, and the consequences of that battle.

Next we are going to look up latitude and longitude values for each of the listed locations.

In [9]:
# import and set up libraries
!pip install geopy --user
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter
locator = Nominatim(user_agent='Callysto Geocoder')
geocode = RateLimiter(locator.geocode, min_delay_seconds=.1)
location_data_dictionary = {} # an empty dictionary that we will add to
# loop through the unique locations in the previous dataframe and geocode their location
for place in revolution_data['Colony/State'].unique():
    #location = locator.geocode(place) # without rate limiting
    location = geocode(place)
    print(location)
    location_data_dictionary.update({place:location})
# clear the screen of the progress we were printing
from IPython import display
display.clear_output()
# create the dataframe
location_data = pd.DataFrame(data=location_data_dictionary).transpose()
location_data.rename(columns={0:'Location', 1:'Coordinates'}, inplace=True)
location_data

Location  \
Massachusetts            Massachusetts, United States of America   
New Hampshire            New Hampshire, United States of America   
Virginia                      Virginia, United States of America   
New York                      New York, United States of America   
Quebec                                            Québec, Canada   
...                                                          ...   
Delaware Bay   Delaware Bay, Cumberland County, New Jersey, U...   
Hispaniola     La Hispaniola, Constanza, La Vega, República D...   
Cape May       Cape May, Cape May County, New Jersey, 18204, ...   
Guadeloupe                                    Guadeloupe, France   
Cuba                                                        Cuba   

                                            Coordinates  
Massachusetts                  (42.3788774, -72.032366)  
New Hampshire                 (43.4849133, -71.6553992)  
Virginia                      (37.1232245, -78.4927721)  
New York                      (40.7127281, -74.0060152)  
Quebec                        (52.4760892, -71.8258668)  
...                                                 ...  
Delaware Bay   (39.247595399999994, -75.30105997051399)  
Hispaniola             (18.77858115, -70.5427697709766)  
Cape May                      (38.9351126, -74.9060053)  
Guadeloupe                    (16.2490067, -61.5650444)  
Cuba                          (23.0131338, -80.8328748)  

[62 rows x 2 columns]

## Geographic View of The American Revolution

Now that we have some location data about the Revolutionary War battles, let's put it on a map.

In [3]:
# join our two dataframes together
map_data = revolution_data.join(location_data, on='Colony/State')
# split the Coordinates column into Latitude and Longitude
map_data[['Latitude','Longitude']] = pd.DataFrame(map_data['Coordinates'].tolist(), index=map_data.index)
# create the map
import folium
battle_map = folium.Map(location=[50, -50], zoom_start=2)
for i, row in map_data.iterrows():
    location=[row['Latitude'], row['Longitude']]
    battle_map.add_child(folium.Marker(location, tooltip=row['Battle'], popup=row['Date']))
battle_map

It is interesting to note that that not all of the battles took place in the United States.

We can list the battles that took place in Canada.

In [4]:
map_data[map_data['Location'].str.contains('Canada')]

Battle                            Date  \
10       Siege of Fort St. Jean  September 17 –November 3, 1775   
11      Battle of Longue-Pointe              September 25, 1775   
18             Battle of Quebec               December 31, 1775   
23       Battle of Saint-Pierre                  March 25, 1776   
25         Battle of The Cedars                 May 18–27, 1776   
26     Battle of Trois-Rivières                    June 8, 1776   
37    Battle of Fort Cumberland            November 10–29, 1776   
107       Battle of Chillicothe                        May 1779   
154           Battle of Pekowee                  August 8, 1780   
170           La Balme's Defeat                November 5, 1780   
199  Naval battle of Louisbourg                   July 21, 1781   
203             Lochry's Defeat                 August 24, 1781   
234         Crawford expedition            May 25-June 12, 1782   
235    Naval battle off Halifax                 May 28–29, 1782   
236             Raid on Chester                   June 30, 1782   
237           Raid on Lunenburg                    July 1, 1782   
239       Hudson Bay Expedition                  August 8, 1782   

             Colony/State                                            Outcome  \
10                 Quebec  Patriot victory: Patriots capture British forc...   
11                 Quebec                                    British victory   
18                 Quebec  British victory: British repulse Patriot assau...   
23                 Quebec                                    Patriot victory   
25                 Quebec                                    British victory   
26                 Quebec  British victory: Patriots forced to evacuate Q...   
37            Nova Scotia                                    British victory   
107                Quebec                                    Patriot victory   
154                Quebec                                    Patriot victory   
170                Quebec                           British-Iroquois victory   
199           Nova Scotia                             Franco-Patriot victory   
203                Quebec                           British-Iroquois victory   
234                Quebec                           British-Iroquois victory   
235           Nova Scotia                                    British victory   
236  Chester, Nova Scotia                                    British victory   
237           Nova Scotia                                    Patriot victory   
239         Rupert's Land                             Franco-Patriot victory   

                                              Location  \
10                                      Québec, Canada   
11                                      Québec, Canada   
18                                      Québec, Canada   
23                                      Québec, Canada   
25                                      Québec, Canada   
26                                      Québec, Canada   
37                                 Nova Scotia, Canada   
107                                     Québec, Canada   
154                                     Québec, Canada   
170                                     Québec, Canada   
199                                Nova Scotia, Canada   
203                                     Québec, Canada   
234                                     Québec, Canada   
235                                Nova Scotia, Canada   
236  Chester, Chester District Municipality, Nova S...   
237                                Nova Scotia, Canada   
239  Anglican Centre, Diocese of Rupert's Land, 935...   

                          Coordinates   Latitude  Longitude  
10          (52.4760892, -71.8258668)  52.476089 -71.825867  
11          (52.4760892, -71.8258668)  52.476089 -71.825867  
18          (52.4760892, -71.8258668)  52.476089 -71.825867  
23          (52.4760892, -71.8258668)  52.476089 -71.825867  
25          (52.476089

We are also interested in looking at the battles by year, so we will create a `year` column from the last four characters of the `Date` column.

In [5]:
map_data['Year'] = map_data['Date'].str[-4:]
map_data

Battle                            Date  \
0                         Powder Alarm*               September 1, 1774   
1    Storming of Fort William and Mary*               December 14, 1774   
2      Battles of Lexington and Concord                  April 19, 1775   
3                       Siege of Boston  April 19, 1775 –March 17, 1776   
4                   Gunpowder Incident*                  April 20, 1775   
..                                  ...                             ...   
253            Action of 2 January 1783                 January 2, 1783   
254           Action of 22 January 1783                January 22, 1783   
255          Action of 15 February 1783               February 15, 1783   
256          Action of 17 February 1783                17 February 1783   
257            Recapture of the Bahamas                14–18 April 1783   

      Colony/State                                            Outcome  \
0    Massachusetts          British soldiers remove military supplies   
1    New Hampshire  Patriots seize powder and shot after brief ski...   
2    Massachusetts  Patriot victory: British forces raiding Concor...   
3    Massachusetts  Patriot victory: British eventually evacuate B...   
4         Virginia  Virginia governor Lord Dunmore removes powder ...   
..             ...                                                ...   
253     Hispaniola                                       Inconclusive   
254       Virginia                                    British victory   
255     Guadeloupe                                    British victory   
256           Cuba                                    British victory   
257        Bahamas                                    British victory   

                                              Location  \
0              Massachusetts, United States of America   
1              New Hampshire, United States of America   
2              Massachusetts, United States of America   
3              Massachusetts, United States of America   
4                   Virginia, United States of America   
..                                                 ...   
253  La Hispaniola, Constanza, La Vega, República D...   
254                 Virginia, United States of America   
255                                 Guadeloupe, France   
256                                               Cuba   
257                                        The Bahamas   

                          Coordinates   Latitude  Longitude  Year  
0            (42.3788774, -72.032366)  42.378877 -72.032366  1774  
1           (43.4849133, -71.6553992)  43.484913 -71.655399  1774  
2            (42.3788774, -72.032366)  42.378877 -72.032366  1775  
3            (42.3788774, -72.032366)  42.378877 -72.032366  1776  
4           (37.1232245, -78.4927721)  37.123224 -78.492772  1775  
..                                ...        ...        ...   ...  
253  (18.77858115, -70.5427697709766)  18.778581 -70.542770  1783  
254         (37.1232245, -78.4927721)  37.123224 -78.492772  1783  
255         (16.2490067, -61.5650444)  16.249007 -61.565044  1783  
256         (23.0131338, -80.8328748)  23.013134 -80.832875  1783  
257         (24.7736546, -78.0000547)  24.773655 -78.000055  1783  

[258 rows x 9 columns]

We can now animate those battles by the year that they took place. The year can be controlled by adjusting the slider on the bottom of the map below, or by simply pressing the play button. Look at the map below and observe the progress of battles that took place.

If you hover your mouse over the battle location, you can see the name of the battle. You can also zoom in and out with the buttons at the top right.

In [6]:
import plotly.express as px
fig = px.scatter_geo(map_data, lat='Latitude', lon='Longitude', animation_frame='Year', hover_name='Battle')
fig.show()

Using this interactive map, you can observe the progression of the American Revolution in North America in terms of the battles fought each year. Pay particular attention to the battles taking place in Quebec, the Maritime provinces, and along the Saint Lawrence River. 


### Questions
1. Use the slider and hover over the battles on the map above, which battles were fought in what is now Canada?
2. Why did some battles of the American Revolution take place in Quebec? 
3. Choose one of those battles and study it further. How might that battle have shaped Canada as we know it today?



## The Progression of the War
While the map above makes it easy to see where and when various battles were fought during the American Revolution, sometimes it's to look at different visualizations. The following bar chart displays how many battles took place each year.

In [7]:
import cufflinks as cf
cf.go_offline()
by_year = map_data.groupby('Year').count()['Battle']
by_year.iplot(kind='bar', yTitle='Number of Battles', xTitle='Year', title='Battles per Year')

We can see that the year 1777 had the most battles out of the entire war. This is because 1776-1777 was the beginning of the British counter offensive, and British forces made considerable progress against the Americans. 

### Questions
1. 1778 has about half as many battles as 1777, the year of the British counter offensive. What is the reason for this?
2. 1780 has the second most battles in a year. What events lead to this year having as many battles as it did?

## American Revolution Battle Locations

We can also chart the number of battles by location.

In [8]:
by_location = map_data.groupby('Location').count()['Battle'].sort_values()
by_location.iplot(kind='barh', margin=(400,0,0,50), dimensions=(800,1100), xTitle='Number of Battles', title='Battles by Location',)

## Summary

Using data from Wikipedia, we were able to visualize the locations and progress of the American Revolution, and also discover how many battles took place each year.

[![Callysto.ca License](https://github.com/callysto/curriculum-notebooks/blob/master/callysto-notebook-banner-bottom.jpg?raw=true)](https://github.com/callysto/curriculum-notebooks/blob/master/LICENSE.md)